In [1]:
import sys
import os
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '../..')))

# Path Configuration
from tools.preprocess import *

# Processing context
trait = "Cervical_Cancer"
cohort = "GSE63678"

# Input paths
in_trait_dir = "../../input/GEO/Cervical_Cancer"
in_cohort_dir = "../../input/GEO/Cervical_Cancer/GSE63678"

# Output paths
out_data_file = "../../output/preprocess/Cervical_Cancer/GSE63678.csv"
out_gene_data_file = "../../output/preprocess/Cervical_Cancer/gene_data/GSE63678.csv"
out_clinical_data_file = "../../output/preprocess/Cervical_Cancer/clinical_data/GSE63678.csv"
json_path = "../../output/preprocess/Cervical_Cancer/cohort_info.json"


### Step 1: Initial Data Loading

In [2]:
from tools.preprocess import *
# 1. Identify the paths to the SOFT file and the matrix file
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)

# 2. Read the matrix file to obtain background information and sample characteristics data
background_prefixes = ['!Series_title', '!Series_summary', '!Series_overall_design']
clinical_prefixes = ['!Sample_geo_accession', '!Sample_characteristics_ch1']
background_info, clinical_data = get_background_and_clinical_data(matrix_file, background_prefixes, clinical_prefixes)

# 3. Obtain the sample characteristics dictionary from the clinical dataframe
sample_characteristics_dict = get_unique_values_by_row(clinical_data)

# 4. Explicitly print out all the background information and the sample characteristics dictionary
print("Background Information:")
print(background_info)
print("Sample Characteristics Dictionary:")
print(sample_characteristics_dict)


Background Information:
!Series_title	"Expression data from Vulvar, Cervical, Endometrial Carcinoma tissue"
!Series_summary	"A growing number of studies on gynecological cancers (GCs) have revealed potential gene markers associated either with the pathogenesis and progression of the disease on representing putative targets for therapy and treatment of cervical (CC), endometrial (EC) and vulvar cancer (VC). However, quite a little overlap is found between these data. In this study we combined data from the three GCs integrating gene expression profile analysis."
!Series_summary	"The meta-analysis including our results and data emerge from other available studies on gynecological malignancies and other cancer types, revealed common properties among them including deregulation of cell cycle, immune response, antiviral response and apoptosis."
!Series_overall_design	"Total RNA was extracted from physiological and cancer patients from cervix, endometrium and vulvar tissue and was hybridized

### Step 2: Dataset Analysis and Clinical Feature Extraction

In [3]:
import pandas as pd
import os
import numpy as np

# Analyzing the dataset for gene expression availability
# Based on the background information, this dataset contains gene expression data from Affymetrix HG133_A_2.0 microarray chips
is_gene_available = True

# Analyzing the sample characteristics dictionary for trait, age, and gender
# From the sample characteristics, we can identify:
# - Row 1 contains disease state which can be used for trait (cancer vs normal)
# - Age is not explicitly provided
# - Gender is not explicitly provided (though all samples are likely female given these are gynecological cancers)

trait_row = 1  # disease state: carcinoma vs normal
age_row = None  # Age is not available
gender_row = None  # Gender is not available

# Define conversion functions for available variables
def convert_trait(value):
    """Convert trait value to binary (0 for normal, 1 for carcinoma)"""
    if value is None:
        return None
    
    # Extract the value after colon if present
    if ':' in value:
        value = value.split(':', 1)[1].strip()
    
    # Convert to binary
    if 'normal' in value.lower():
        return 0
    elif 'carcinoma' in value.lower():
        return 1
    else:
        return None

def convert_age(value):
    """Placeholder function for age conversion (not used)"""
    return None

def convert_gender(value):
    """Placeholder function for gender conversion (not used)"""
    return None

# Validate and save metadata about this cohort
is_trait_available = trait_row is not None
validate_and_save_cohort_info(
    is_final=False,
    cohort=cohort,
    info_path=json_path,
    is_gene_available=is_gene_available,
    is_trait_available=is_trait_available
)

# If clinical data is available, extract and save it
if trait_row is not None:
    try:
        # Assuming clinical_data is available from previous steps
        clinical_data = pd.read_csv(os.path.join(in_cohort_dir, "clinical_data.csv"))
        
        # Extract clinical features
        selected_clinical_df = geo_select_clinical_features(
            clinical_df=clinical_data,
            trait=trait,
            trait_row=trait_row,
            convert_trait=convert_trait,
            age_row=age_row,
            convert_age=convert_age,
            gender_row=gender_row,
            convert_gender=convert_gender
        )
        
        # Preview the extracted clinical data
        preview = preview_df(selected_clinical_df)
        print("Preview of extracted clinical data:")
        print(preview)
        
        # Create the directory if it doesn't exist
        os.makedirs(os.path.dirname(out_clinical_data_file), exist_ok=True)
        
        # Save the extracted clinical data
        selected_clinical_df.to_csv(out_clinical_data_file, index=False)
        print(f"Clinical data saved to {out_clinical_data_file}")
    except Exception as e:
        print(f"Error extracting clinical features: {str(e)}")
else:
    print("No clinical data available for this cohort.")


Error extracting clinical features: [Errno 2] No such file or directory: '../../input/GEO/Cervical_Cancer/GSE63678/clinical_data.csv'


### Step 3: Gene Data Extraction

In [4]:
# 1. Use the get_genetic_data function from the library to get the gene_data from the matrix_file previously defined.
gene_data = get_genetic_data(matrix_file)

# 2. Print the first 20 row IDs (gene or probe identifiers) for future observation.
print(gene_data.index[:20])


Index(['1007_s_at', '1053_at', '117_at', '121_at', '1255_g_at', '1294_at',
       '1316_at', '1320_at', '1405_i_at', '1431_at', '1438_at', '1487_at',
       '1494_f_at', '1598_g_at', '160020_at', '1729_at', '1773_at', '177_at',
       '179_at', '1861_at'],
      dtype='object', name='ID')


### Step 4: Gene Identifier Review

In [5]:
# Here I need to determine if the gene identifiers need mapping to standard gene symbols

# The identifiers appear to be Affymetrix probe IDs (e.g., "1007_s_at", "1053_at")
# These are not standard human gene symbols, which would look like "BRCA1", "TP53", etc.
# Affymetrix probe IDs require mapping to standard gene symbols

requires_gene_mapping = True


### Step 5: Gene Annotation

In [6]:
# 1. Use the 'get_gene_annotation' function from the library to get gene annotation data from the SOFT file.
gene_annotation = get_gene_annotation(soft_file)

# 2. Use the 'preview_df' function from the library to preview the data and print out the results.
print("Gene annotation preview:")
print(preview_df(gene_annotation))


Gene annotation preview:
{'ID': ['1007_s_at', '1053_at', '117_at', '121_at', '1255_g_at'], 'GB_ACC': ['U48705', 'M87338', 'X51757', 'X69699', 'L36861'], 'SPOT_ID': [nan, nan, nan, nan, nan], 'Species Scientific Name': ['Homo sapiens', 'Homo sapiens', 'Homo sapiens', 'Homo sapiens', 'Homo sapiens'], 'Annotation Date': ['Oct 6, 2014', 'Oct 6, 2014', 'Oct 6, 2014', 'Oct 6, 2014', 'Oct 6, 2014'], 'Sequence Type': ['Exemplar sequence', 'Exemplar sequence', 'Exemplar sequence', 'Exemplar sequence', 'Exemplar sequence'], 'Sequence Source': ['Affymetrix Proprietary Database', 'GenBank', 'Affymetrix Proprietary Database', 'GenBank', 'Affymetrix Proprietary Database'], 'Target Description': ['U48705 /FEATURE=mRNA /DEFINITION=HSU48705 Human receptor tyrosine kinase DDR gene, complete cds', 'M87338 /FEATURE= /DEFINITION=HUMA1SBU Human replication factor C, 40-kDa subunit (A1) mRNA, complete cds', "X51757 /FEATURE=cds /DEFINITION=HSP70B Human heat-shock protein HSP70B' gene", 'X69699 /FEATURE= /DEF

### Step 6: Gene Identifier Mapping

In [7]:
# 1. Observe the columns in gene annotation data and determine which columns to use for mapping
# From the preview, we can see:
# - 'ID' column contains the probe IDs (e.g., '1007_s_at') which match the gene_data index
# - 'Gene Symbol' column contains the gene symbols (e.g., 'DDR1 /// MIR4640')

# 2. Extract the gene mapping dataframe using get_gene_mapping
gene_mapping = get_gene_mapping(gene_annotation, prob_col='ID', gene_col='Gene Symbol')

# 3. Apply the gene mapping to convert probe-level measurements to gene expression data
# This handles the many-to-many relationships between probes and genes
gene_data = apply_gene_mapping(gene_data, gene_mapping)

# Print the shape of the resulting gene expression dataframe and preview some gene symbols
print(f"Gene expression data shape after mapping: {gene_data.shape}")
print("Sample of gene symbols after mapping:")
print(gene_data.index[:10])


Gene expression data shape after mapping: (13830, 35)
Sample of gene symbols after mapping:
Index(['A1CF', 'A2M', 'A4GALT', 'A4GNT', 'AAAS', 'AACS', 'AADAC', 'AAGAB',
       'AAK1', 'AAMDC'],
      dtype='object', name='Gene')


### Step 7: Data Normalization and Linking

In [8]:
# 1. Normalize the obtained gene data with the 'normalize_gene_symbols_in_index' function from the library.
normalized_gene_data = normalize_gene_symbols_in_index(gene_data)
os.makedirs(os.path.dirname(out_gene_data_file), exist_ok=True)
normalized_gene_data.to_csv(out_gene_data_file)
print(f"Normalized gene data saved to {out_gene_data_file}")

# Extract clinical features directly from the matrix file data (reuse the data from previous steps)
background_info, clinical_data = get_background_and_clinical_data(matrix_file)

# Define the function to convert trait values (carcinoma vs normal)
def convert_trait(value):
    """Convert trait value to binary (0 for normal, 1 for carcinoma)"""
    if value is None:
        return None
    
    # Extract the value after colon if present
    if ':' in value:
        value = value.split(':', 1)[1].strip()
    
    # Convert to binary
    if 'normal' in value.lower():
        return 0
    elif 'carcinoma' in value.lower():
        return 1
    else:
        return None

# Extract clinical features using the trait_row identified in Step 2
selected_clinical_df = geo_select_clinical_features(
    clinical_df=clinical_data,
    trait=trait,
    trait_row=1,  # disease state: carcinoma vs normal
    convert_trait=convert_trait
)

# Save clinical data
os.makedirs(os.path.dirname(out_clinical_data_file), exist_ok=True)
selected_clinical_df.to_csv(out_clinical_data_file)
print(f"Clinical data saved to {out_clinical_data_file}")

# Now link the clinical and genetic data
linked_data = geo_link_clinical_genetic_data(selected_clinical_df, normalized_gene_data)
print("Linked data shape:", linked_data.shape)

# Handle missing values in the linked data
linked_data = handle_missing_values(linked_data, trait)

# 4. Determine whether the trait and some demographic features are severely biased, and remove biased features.
is_trait_biased, unbiased_linked_data = judge_and_remove_biased_features(linked_data, trait)

# 5. Conduct quality check and save the cohort information.
is_usable = validate_and_save_cohort_info(
    is_final=True, 
    cohort=cohort, 
    info_path=json_path, 
    is_gene_available=True, 
    is_trait_available=True, 
    is_biased=is_trait_biased, 
    df=unbiased_linked_data,
    note="Dataset contains cervical, endometrial, and vulvar tissue samples with carcinoma and normal conditions."
)

# 6. If the linked data is usable, save it as a CSV file to 'out_data_file'.
if is_usable:
    os.makedirs(os.path.dirname(out_data_file), exist_ok=True)
    unbiased_linked_data.to_csv(out_data_file)
    print(f"Linked data saved to {out_data_file}")
else:
    print("Data was determined to be unusable and was not saved")

Normalized gene data saved to ../../output/preprocess/Cervical_Cancer/gene_data/GSE63678.csv
Clinical data saved to ../../output/preprocess/Cervical_Cancer/clinical_data/GSE63678.csv
Linked data shape: (35, 13543)


For the feature 'Cervical_Cancer', the least common label is '0.0' with 17 occurrences. This represents 48.57% of the dataset.
The distribution of the feature 'Cervical_Cancer' in this dataset is fine.



Linked data saved to ../../output/preprocess/Cervical_Cancer/GSE63678.csv
